In [ ]:
import numpy as np
import pandas as pd
import json
import requests
import pickle

import pymongo
from pymongo import MongoClient

In [ ]:
from google.colab import drive

In [ ]:
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
zipcodes_df = pd.read_csv('/content/drive/MyDrive/Data_Engineering_Realtor/zipcodes.csv')
zipcodes = zipcodes_df.iloc[:,0].tolist()

In [ ]:
zipcodes[:5]

[90011, 91331, 90650, 90201, 90044]

In [ ]:
len(zipcodes)

1741

**API: Pull active listings**

In [ ]:
sales_list = []

In [ ]:
#API: pull active listings
    
url = "https://us-real-estate.p.rapidapi.com/for-sale"
    
for zip_ in zipcodes:
    querystring = {"offset":"0","limit":"200","state_code":"CA","city":"<REQUIRED>","location":zip_,"sort":"newest"}
    headers = {
    'x-rapidapi-key': "562dd28a05msh370f0f807730589p1380f1jsneebd1857de2a",
    'x-rapidapi-host': "us-real-estate.p.rapidapi.com"
    } 
        
    response = requests.request("GET", url, headers=headers, params=querystring)
    sales_list.append(response.json()['data']['results']) 

In [ ]:
sales_all = sales_list

In [ ]:
#pick_insert = open('drive/My Drive/Data_Engineering_Realtor/sales_all.pickle','wb')

In [ ]:
#pickle.dump(sales_all, pick_insert)

In [ ]:
#sales_plk = open('drive/My Drive/Data_Engineering_Realtor/sales_all.pickle','rb')

In [ ]:
#sales = pickle.load(sales_plk)

**API: Pull sold listings**

In [ ]:
sold_list = []

In [ ]:
#API: Pull sold listings

url = "https://us-real-estate.p.rapidapi.com/sold-homes"

for zip_ in zipcodes[1718:]:
    querystring = {"state_code":"CA","city":"<REQUIRED>","location":zip_,"limit":"200","offset":"0","sort":"sold_date"}

    headers = {
        'x-rapidapi-key': "562dd28a05msh370f0f807730589p1380f1jsneebd1857de2a",
        'x-rapidapi-host': "us-real-estate.p.rapidapi.com"
        }

    response = requests.request("GET", url, headers=headers, params=querystring)
    sold_list.append(response.json()['data']['results']) 

In [ ]:
sold_all = sold_list

In [ ]:
pick_insert = open('drive/My Drive/Data_Engineering_Realtor/sold_all.pickle','wb')

In [ ]:
pickle.dump(sold_all, pick_insert)

In [ ]:
#sold_plk = open('drive/My Drive/Data_Engineering_Realtor/sold_all.pickle','rb')

In [ ]:
#sold = pickle.load(sold_plk)

**Upload data into Mongodb**

In [ ]:
#! python -m pip install pymongo==3.7.2

In [ ]:
#!apt install mongodb >log
#!service mongodb start



 * Starting database mongodb
   ...done.


In [ ]:
# Imports datetime library

import pymongo
from pymongo import MongoClient


In [ ]:
client = MongoClient()

In [ ]:
sales_plk = open('drive/My Drive/Data_Engineering_Realtor/sales_all.pickle','rb')
sales_all = pickle.load(sales_plk)

In [ ]:
db = client.sales
sales = db.active_listing

In [ ]:
for i in sales_all:
  if not i:
    continue
  else:
      sales.insert_many(i)


In [ ]:
len(list(sales.find({},{'listing_id':1, '_id':0})))

242290

In [ ]:
#sold_plk = open('drive/My Drive/Data_Engineering_Realtor/sold_all.pickle','rb')
#sold_all = pickle.load(sold_plk)

**Upload data into Mongodb**

In [ ]:
db = client.sold
sold = db.closed_listing

In [ ]:
for i in sold_all:
  if not i:
    continue
  else:
      sold.insert_many(i)

In [ ]:
sold.count_documents({})

243198

In [ ]:
list(sold.find({},{'_id':0}))

[{'branding': [{'name': 'COMPASS', 'photo': None, 'type': 'Office'}],
  'community': None,
  'description': {'baths': 3,
   'baths_1qtr': None,
   'baths_3qtr': None,
   'baths_full': 2,
   'baths_half': 1,
   'beds': 3,
   'garage': None,
   'lot_sqft': 2949,
   'name': None,
   'sold_date': '2021-07-16',
   'sold_price': 1760000,
   'sqft': 1648,
   'stories': 2,
   'sub_type': None,
   'type': 'single_family',
   'year_built': 1926},
  'flags': {'is_coming_soon': None,
   'is_contingent': None,
   'is_for_rent': None,
   'is_foreclosure': None,
   'is_new_construction': None,
   'is_new_listing': False,
   'is_pending': None,
   'is_plan': None,
   'is_price_reduced': None,
   'is_subdivision': None},
  'last_update_date': '2021-07-16T12:02:52Z',
  'lead_attributes': {'show_contact_an_agent': True},
  'list_date': '2021-06-15T15:05:55Z',
  'list_price': 1549000,
  'listing_id': '2930532060',
  'location': {'address': {'city': 'Los Angeles',
    'coordinate': {'lat': 34.08511, 'lon':

In [ ]:
tmp = list(sold.find({}, {'_id':0, 'listing_id':1, 'property_id':1, 'description':1, 'list_date':1, 'list_price':1, 'location':1, 'status':1,'tags':1}))

In [ ]:
#Convert collections into dataframe
tmp_df = pd.json_normalize(tmp)

In [ ]:
tmp_df.head()

tags  ... location.county
0  [central_air, central_heat, community_outdoor_...  ...             NaN
1  [central_air, central_heat, city_view, communi...  ...             NaN
2  [central_air, central_heat, community_outdoor_...  ...             NaN
3  [community_outdoor_space, community_security_f...  ...             NaN
4  [central_air, central_heat, community_outdoor_...  ...             NaN

[5 rows x 33 columns]

In [ ]:
tmp_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 243198 entries, 0 to 243197
Data columns (total 33 columns):
 #   Column                           Non-Null Count   Dtype  
---  ------                           --------------   -----  
 0   tags                             242474 non-null  object 
 1   status                           243198 non-null  object 
 2   list_date                        243195 non-null  object 
 3   list_price                       243185 non-null  float64
 4   property_id                      243198 non-null  object 
 5   listing_id                       243198 non-null  object 
 6   description.year_built           231423 non-null  float64
 7   description.baths_3qtr           13964 non-null   float64
 8   description.sold_date            243198 non-null  object 
 9   description.sold_price           243198 non-null  int64  
 10  description.baths_full           226811 non-null  float64
 11  description.name                 0 non-null       object 
 12  de

In [ ]:
sold_df_features= ['property_id', 'listing_id', 'status', 'list_date','list_price', 'description.sold_price','description.year_built', 'description.baths_3qtr', 'description.sold_date',
                 'description.baths_full','description.baths_half','description.lot_sqft','description.sqft','description.baths','description.type','description.sub_type','description.baths_1qtr','description.garage',
                 'description.stories','description.beds','location.address.postal_code','location.address.state','location.address.coordinate.lon','location.address.coordinate.lat',
                 'location.address.city','location.address.state_code','location.address.line','location.county.fips_code','location.county.name']

In [ ]:
sold_df = tmp_df[sold_df_features]


In [ ]:
#Save final closed listing data into csv
#sold_df.to_csv("drive/My Drive/Data_Engineering_Realtor/closed_listings.csv", index = False)

In [ ]:
sales_plk = open('drive/My Drive/Data_Engineering_Realtor/sales_all.pickle','rb')
sales_all = pickle.load(sales_plk)

In [ ]:
#client.drop_database('sales')

In [ ]:
db = client.sales
sales = db.active_listing

In [ ]:
for i in sales_all:
  if not i:
    continue
  else:
    sales.insert_many(i)

In [ ]:
sales.count_documents({})

242290

In [ ]:
tmp2 = list(sales.find({}, {'_id':0, 'description':1, 'list_date':1, 'list_price':1, 'location':1, 'property_id':1, 'listing_id':1, 'status':1}))

In [ ]:
tmp2_df = pd.json_normalize(tmp2)

tmp2_df.head()

status             list_date  ...  location.county.name location.county
0  for_sale  2021-07-17T03:04:48Z  ...           Los Angeles             NaN
1  for_sale  2021-07-17T02:49:37Z  ...           Los Angeles             NaN
2  for_sale  2021-07-17T02:45:24Z  ...           Los Angeles             NaN
3  for_sale  2021-07-17T01:15:16Z  ...           Los Angeles             NaN
4  for_sale  2021-07-17T00:20:13Z  ...           Los Angeles             NaN

[5 rows x 31 columns]

In [ ]:
tmp2_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 242290 entries, 0 to 242289
Data columns (total 31 columns):
 #   Column                           Non-Null Count   Dtype  
---  ------                           --------------   -----  
 0   status                           242290 non-null  object 
 1   list_date                        242290 non-null  object 
 2   list_price                       242052 non-null  float64
 3   property_id                      242290 non-null  object 
 4   listing_id                       240749 non-null  object 
 5   description.baths_3qtr           12790 non-null   float64
 6   description.year_built           214385 non-null  float64
 7   description.sold_price           186268 non-null  float64
 8   description.baths_full           214862 non-null  float64
 9   description.name                 1541 non-null    object 
 10  description.baths_half           54432 non-null   float64
 11  description.lot_sqft             218922 non-null  float64
 12  de

In [ ]:
sale_df_features= ['property_id', 'listing_id', 'status', 'list_date','list_price','description.year_built', 'description.baths_3qtr', 'description.baths_full',
                  'description.baths_half','description.lot_sqft','description.sqft','description.baths','description.type','description.sub_type','description.baths_1qtr','description.garage',
                 'description.stories','description.beds','location.address.postal_code','location.address.state','location.address.coordinate.lon','location.address.coordinate.lat',
                 'location.address.city','location.address.state_code','location.address.line','location.county.fips_code','location.county.name']

In [ ]:
sales_df = tmp2_df[sale_df_features]

In [ ]:
#Save final closed listing data into csv
#sales_df.to_csv("drive/My Drive/Data_Engineering_Realtor/active_listings.csv", index = False)